In [87]:
import pandas as pd
import numpy as np

#df = pd.read_csv('addresses.csv')
#print(df.columns)

import pandas as pd
df = pd.read_csv('trainingset.csv', sep=',', low_memory = False).head(200000)
df = df.rename(columns={'bbl_id': 'building_id', "bldg_ctgy": "building_category", "tax_cls_p": "tax_class_present", "bldg_cls_p": "building_class_present", "res_unit": "residential_unit", "com_unit" : "community_unit", "tot_unit" : "total_units", "yr_built" : "year_built", "tax_cls_s": "tax_class_sale", "bldg_cls_s" : "building_class_sale"})
print(df.columns)
id = df[['building_id', 'price']]
df = df[df['price']>75000]
df['tax_class_sale'] = df['tax_class_sale'].replace([1,2,3,4], [20.9, 12.6, 12.1, 10.5])

print(df['long'])



Index([u'Unnamed: 0', u'Unnamed: 0.1', u'Unnamed: 0_x', u'Sale_id_x',
       u'building_id', u'year', u'borough', u'building_category',
       u'tax_class_present', u'block', u'lot', u'easmnt',
       u'building_class_present', u'address', u'apt', u'zip',
       u'residential_unit', u'community_unit', u'total_units', u'land_sqft',
       u'tot_sqft', u'year_built', u'tax_class_sale', u'building_class_sale',
       u'sale_date', u'price', u'usable', u'long', u'lat', u'Unnamed: 0_y',
       u'Sale_id_y', u'0', u'1', u'2', u'3', u'4', u'5', u'6', u'7', u'8',
       u'9', u'10', u'11', u'12', u'13', u'14', u'15', u'16', u'17', u'18',
       u'19', u'20', u'21', u'22', u'23', u'24', u'25', u'26', u'27', u'28',
       u'29', u'30', u'31'],
      dtype='object')
2        -73.979713
3        -73.979713
8        -73.979713
9        -73.979713
10       -73.977532
17       -73.979713
23       -73.979713
25       -73.979713
27       -73.977532
28       -73.979713
29       -73.979713
31       -73.9

In [88]:
import re
df['sale_date'] = df['sale_date'].apply(lambda x: re.sub(r'/','-', str(x)))
df['sale_date'] = df['sale_date'].apply(lambda x: re.sub(r'-[0-9]{2}-[0-9]{4}$','', str(x)))
df['sale_date'] = df['sale_date'].apply(lambda x: re.sub(r'-[0-9]{2}-[0-9]{4}$','', str(x)))
df['sale_date'] = df['sale_date'].apply(lambda x: re.sub(r'-','', str(x)))
df['sale_date'] = df['sale_date'].astype('int64')
df = df[df['sale_date'] < 13]
print(df.head())
df2 = df

print(df['long'])

    Unnamed: 0  Unnamed: 0.1  Unnamed: 0_x  Sale_id_x  building_id    year  \
2            2       2976484         42432    42433.0  110061303.0  2015.0   
3            3       1481479         41194    41195.0  110061302.0  2015.0   
9            9       3098587         42518    42519.0  110061303.0  2015.0   
10          10        195925         40046    40047.0    1100937.0  2015.0   
17          17       2382082         41955    41956.0  110061302.0  2015.0   

    borough building_category tax_class_present   block    ...           22  \
2       1.0  45  CONDO HOTELS                 4  1006.0    ...     0.301583   
3       1.0  45  CONDO HOTELS                 4  1006.0    ...     0.301583   
9       1.0  45  CONDO HOTELS                 4  1006.0    ...     0.301583   
10      1.0  26  OTHER HOTELS                 4  1009.0    ...     0.347919   
17      1.0  45  CONDO HOTELS                 4  1006.0    ...     0.301583   

          23        24        25        26        27    

In [89]:
df['tax_class_sale'] = df['tax_class_sale'].replace([1,2,3,4], [20.9, 12.6, 12.1, 10.5])

building_category_dummies = pd.get_dummies(df["building_category"], prefix=df["building_category"].name)
df = df.drop(columns="building_category")
df_build_cat = pd.concat([id, building_category_dummies], axis=1)
df = df_build_cat
X = df.drop(columns=['price', 'building_id'])

print(X)

        building_category_01  ONE FAMILY DWELLINGS  \
0                                              NaN   
1                                              NaN   
2                                              0.0   
3                                              0.0   
4                                              NaN   
5                                              NaN   
6                                              NaN   
7                                              NaN   
8                                              NaN   
9                                              0.0   
10                                             0.0   
11                                             NaN   
12                                             NaN   
13                                             NaN   
14                                             NaN   
15                                             NaN   
16                                             NaN   
17                          

In [90]:
# =======================

#X = df.drop(columns=['price', 'Unnamed: 0', 'building_id'])
Y = df.price
#Y = np.array(Y).reshape(-1)

from sklearn.model_selection import train_test_split

In [96]:
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size = .20, random_state = 40)
print(X_train.shape)
print(X_test.shape)

from sklearn.linear_model import LinearRegression
lr = LinearRegression()

(160000, 31)
(40000, 31)


In [97]:
X_train.fillna(0,inplace=True)

/usr/local/lib/python2.7/dist-packages/pandas/core/frame.py:3790: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  downcast=downcast, **kwargs)


In [98]:

# Fitting the model
lr.fit(X_train, y_train)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=1, normalize=False)

In [99]:
# R^2 scores
print('Train:', lr.score(X_train, y_train))
print('Validation:', lr.score(X_test, y_test))

from sklearn.metrics import mean_absolute_error

print('MAE:', mean_absolute_error(y_test, lr.predict(X_test)))

print('Random prediction:', abs(y_test - y_test.mean()).mean() )

('Train:', 0.2760384993850762)


ValueError: Input contains NaN, infinity or a value too large for dtype('float64').